# Trabalho 2 - Erikson Ferreira

## Importações

In [4]:
# Manipulação de dados
import numpy as np
import pandas as pd

# Geração de números aleatórios
import random

In [5]:
# Geração de gráficos
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
import math
#progess bar
from tqdm import tqdm

In [6]:
import plotly.graph_objects as go
import numpy as np

###  Definição da Função de Rastringin

In [7]:
def rastrigin(x, y):
    return 20 + x**2 - 10 * math.cos(2 * math.pi * x) + y**2 - 10 * math.cos(2 * math.pi * y)

###  Hill Climbing

In [5]:
def hill_climbing():
    restarts = 20
    iterations = 1000
    restart_iter = 50
    df_hill_climbing_restart = pd.DataFrame()
    best_solution = None
    best_fitness = float('inf')
    last_best_coord = [0,0,0]
    # for restart in range(restarts):
    x = random.uniform(-5.12, 5.12)
    y = random.uniform(-5.12, 5.12)
    
    for iteration in range(iterations):
        current_fitness = rastrigin(x, y)
        # print(current_fitness)
        
        if current_fitness < best_fitness:
            best_solution = (x, y)
            last_best_coord = [x, y, current_fitness]
            best_fitness = current_fitness
            df_temp = pd.DataFrame(last_best_coord)
            df_hill_climbing_restart = pd.concat([df_hill_climbing_restart, df_temp.T], axis =0).reset_index(drop=True)
        else:
            df_temp = pd.DataFrame(last_best_coord)
            df_hill_climbing_restart = pd.concat([df_hill_climbing_restart, df_temp.T], axis =0).reset_index(drop=True)
        
        # Produzir vizinho
        delta_x = random.gauss(0, 0.1)
        delta_y = random.gauss(0, 0.1)
        neighbor_x = x + delta_x
        neighbor_y = y + delta_y
        
        if -5.12 <= neighbor_x <= 5.12 and -5.12 <= neighbor_y <= 5.12:
            neighbor_fitness = rastrigin(neighbor_x, neighbor_y)
            
            if neighbor_fitness < current_fitness:
                x = neighbor_x
                y = neighbor_y
    
        # Realizar restart
        if iteration % restart_iter == 0:
            x = random.uniform(-5.12, 5.12)
            y = random.uniform(-5.12, 5.12)
    
    return best_solution, df_hill_climbing_restart

### Simulated Annealing

In [6]:
import math
import random


def generate_random_solution():
    x = random.uniform(-5.12, 5.12)
    y = random.uniform(-5.12, 5.12)
    return (x, y)

def generate_neighbor(solution):
    x = solution[0] + random.gauss(0, 0.1)
    y = solution[1] + random.gauss(0, 0.1)
    return (x, y)

def simulated_annealing():
    initial_solution = generate_random_solution()
    current_solution = initial_solution
    best_solution = initial_solution
    current_fitness = rastrigin(current_solution[0], current_solution[1])
    best_fitness = current_fitness
    temperature = 1.0
    cooling_rate = 0.001
    iteration = 0
    last_best_coord = [0,0,0]
    df_simulated_annealing = pd.DataFrame()

    while iteration < 1000:
        # print(iteration)
        for _ in range(100):
        
            neighbor_solution = generate_neighbor(current_solution)
            # print(_)
            if -5.12 <= neighbor_solution[0] <= 5.12 and -5.12 <= neighbor_solution[1] <= 5.12:
              
                neighbor_fitness = rastrigin(neighbor_solution[0], neighbor_solution[1])
                # print(random.random(), math.exp((current_fitness - neighbor_fitness) / max(temperature, 1e-10)))
                if neighbor_fitness < current_fitness or random.random() < math.exp((current_fitness - neighbor_fitness) / max(temperature, 1e-10)):
                    # print(iteration)
                    current_solution = neighbor_solution
                    current_fitness = neighbor_fitness
                    if neighbor_fitness < best_fitness:
                        best_solution = neighbor_solution
                        best_fitness = neighbor_fitness
                        last_best_coord = [best_solution[0],best_solution[1], neighbor_fitness]
                        df_temp = pd.DataFrame(last_best_coord)
                        df_simulated_annealing = pd.concat([df_simulated_annealing, df_temp.T], axis =0).reset_index(drop=True)
                       
                #     else:
                #         
                    
                else:
                    df_temp = pd.DataFrame(last_best_coord)
                    df_simulated_annealing = pd.concat([df_simulated_annealing, df_temp.T], axis =0).reset_index(drop=True)
                    
                    break
        
        iteration += 1
        


        
        if iteration <= 900:
            temperature = 1.0 - (iteration / 900) * cooling_rate
        else:
            temperature = 0.0
        

    return best_solution, df_simulated_annealing



### Genetic Algorithm

In [43]:
def generate_random_solution():
    x = random.uniform(-5.12, 5.12)
    y = random.uniform(-5.12, 5.12)
    return (x, y)

def generate_population(size):
    population = []
    for _ in range(size):
        individual = generate_random_solution()
        population.append(individual)
    return population

def evaluate_fitness(solution):
    x, y = solution
    return rastrigin(x, y)

def selection(population):
    # Seleção dos pais (torneio binário)
    parent1 = random.choice(population)
    parent2 = random.choice(population)
    if evaluate_fitness(parent1) < evaluate_fitness(parent2):
        return parent1
    else:
        return parent2

def crossover(parent1, parent2):
    # Crossover com média ponderada
    alpha = random.uniform(0, 1)
    x1, y1 = parent1
    x2, y2 = parent2
    child1 = (alpha * x1 + (1 - alpha) * x2, alpha * y1 + (1 - alpha) * y2)
    child2 = (alpha * x2 + (1 - alpha) * x1, alpha * y2 + (1 - alpha) * y1)
    return child1, child2

def mutation(solution):
    # Mutação com adição de ruído gaussiano
    x, y = solution
    x += random.gauss(0, 0.1)
    y += random.gauss(0, 0.1)
    return x, y

def genetic_algorithm():
    population_size = 20
    num_generations = 50
    mutation_rate = 0.3

    population = generate_population(population_size)
    best_solution = None
    best_fitness = float('inf')
    historico = []
    df_genetic_algorithm = pd.DataFrame()

    for _ in range(num_generations):
        new_population = []

        for _ in range(population_size // 2):
            parent1 = selection(population)
            parent2 = selection(population)

            child1, child2 = crossover(parent1, parent2)

            if random.random() < mutation_rate:
                child1 = mutation(child1)
            if random.random() < mutation_rate:
                child2 = mutation(child2)

            new_population.append(child1)
            new_population.append(child2)

        population = new_population

        # Avaliar a aptidão da nova população e atualizar a melhor solução
        for solution in population:
            fitness = evaluate_fitness(solution)
            if fitness < best_fitness:
                best_solution = solution
                best_fitness = fitness
                historico.append(population)
            else:
                historico.append(population)
                
    df_temp = pd.DataFrame([historico])
    df_genetic_algorithm = pd.concat([df_genetic_algorithm, df_temp.T], axis =0).reset_index(drop=True)
    return best_solution, df_genetic_algorithm



#### Minimizando a função

In [8]:
solution_hill_climbing, df_hill_climbing = hill_climbing()
solution_hill_climbing, df_hill_climbing

((-0.001877904624387232, -0.008136011790239789),
             0         1          2
 0    4.642039 -1.055403  39.537191
 1    0.105900 -0.069848   3.097016
 2   -0.033154  0.049590   0.701250
 3   -0.033154  0.049590   0.701250
 4   -0.033154  0.049590   0.701250
 ..        ...       ...        ...
 995 -0.001878 -0.008136   0.013829
 996 -0.001878 -0.008136   0.013829
 997 -0.001878 -0.008136   0.013829
 998 -0.001878 -0.008136   0.013829
 999 -0.001878 -0.008136   0.013829
 
 [1000 rows x 3 columns])

In [9]:
df_hill_climbing.columns = ['x', 'y', 'z']
df_hill_climbing
df_hill_climbing.to_csv

<bound method NDFrame.to_csv of             x         y          z
0    4.642039 -1.055403  39.537191
1    0.105900 -0.069848   3.097016
2   -0.033154  0.049590   0.701250
3   -0.033154  0.049590   0.701250
4   -0.033154  0.049590   0.701250
..        ...       ...        ...
995 -0.001878 -0.008136   0.013829
996 -0.001878 -0.008136   0.013829
997 -0.001878 -0.008136   0.013829
998 -0.001878 -0.008136   0.013829
999 -0.001878 -0.008136   0.013829

[1000 rows x 3 columns]>

In [51]:
def plot_rastrigin_hill_climbing():
    x = np.linspace(-5.12, 5.12, 100)
    y = np.linspace(-5.12, 5.12, 100)
    X, Y = np.meshgrid(x, y)
    Z = 20 + X**2 - 10 * np.cos(2 * np.pi * X) + Y**2 - 10 * np.cos(2 * np.pi * Y)
    
    fig = go.Figure(data=[go.Surface(x=X, y=Y, z=Z, opacity=0.1)])
    fig.update_layout(title='Redução por Hill Climbing', autosize=False,
                      scene=dict(xaxis=dict(title='X'), yaxis=dict(title='Y'), zaxis=dict(title='Z')),
                      width=800, height=800)
    # fig.update_traces(contours_z=dict(show=True, usecolormap=True,
    #                               highlightcolor="limegreen", project_z=True))
    fig.add_trace(go.Scatter3d(x=[df_hill_climbing['x'].iloc[-1]],
                 y=[df_hill_climbing['y'].iloc[-1]],
                 z=[df_hill_climbing['z'].iloc[-1]],
                 ))
    fig.show()

# Plot da função de Rastrigin
plot_rastrigin_hill_climbing()

In [15]:
solution_simulated_annealing, df_simulated_annealing = simulated_annealing()
solution_simulated_annealing, df_simulated_annealing
df_simulated_annealing.columns = ['x', 'y', 'z']

In [16]:
def plot_rastrigin_simulated_annealing():
    x = np.linspace(-5.12, 5.12, 100)
    y = np.linspace(-5.12, 5.12, 100)
    X, Y = np.meshgrid(x, y)
    Z = 20 + X**2 - 10 * np.cos(2 * np.pi * X) + Y**2 - 10 * np.cos(2 * np.pi * Y)
    
    fig = go.Figure(data=[go.Surface(x=X, y=Y, z=Z, opacity=0.1)])
    fig.update_layout(title='Redução por Simulated Annealing', autosize=False,
                      scene=dict(xaxis=dict(title='X'), yaxis=dict(title='Y'), zaxis=dict(title='Z')),
                      width=800, height=800)
    # fig.update_traces(contours_z=dict(show=True, usecolormap=True,
    #                               highlightcolor="limegreen", project_z=True))
    fig.add_trace(go.Scatter3d(x=[df_simulated_annealing['x'].iloc[-1]],
                 y=[df_simulated_annealing['y'].iloc[-1]],
                 z=[df_simulated_annealing['z'].iloc[-1]],
                 ))
    fig.show()

# Plot da função de Rastrigin
plot_rastrigin_simulated_annealing()

In [44]:
solution_genetic_algorithm, df_genetic_algorithm = genetic_algorithm()
solution_genetic_algorithm, df_genetic_algorithm
df_genetic_algorithm.columns = ['population']
df_genetic_algorithm['x'] = 0
df_genetic_algorithm['y'] = 0
df_genetic_algorithm['result'] = 0

for idx, population in df_genetic_algorithm.iterrows():
    menor = float('inf')
    for point in population['population']:
        val = rastrigin(point[0], point[1])
        
        if val < menor:
            menor = val
            df_genetic_algorithm['x'][idx] = point[0]
            df_genetic_algorithm['y'][idx] = point[1]
            df_genetic_algorithm['result'][idx] = menor


df_ga_min = df_genetic_algorithm.min()

C:\Users\eriks\AppData\Local\Temp\ipykernel_24332\2255403977.py:15: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\eriks\AppData\Local\Temp\ipykernel_24332\2255403977.py:16: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\eriks\AppData\Local\Temp\ipykernel_24332\2255403977.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [45]:
def plot_rastrigin_genetic_algorithm():
    x = np.linspace(-5.12, 5.12, 100)
    y = np.linspace(-5.12, 5.12, 100)
    X, Y = np.meshgrid(x, y)
    Z = 20 + X**2 - 10 * np.cos(2 * np.pi * X) + Y**2 - 10 * np.cos(2 * np.pi * Y)
    
    fig = go.Figure(data=[go.Surface(x=X, y=Y, z=Z, opacity=0.1)])
    fig.update_layout(title='Redução por Genetic Algorithm', autosize=False,
                      scene=dict(xaxis=dict(title='X'), yaxis=dict(title='Y'), zaxis=dict(title='Z')),
                      width=800, height=800)
    # fig.update_traces(contours_z=dict(show=True, usecolormap=True,
    #                               highlightcolor="limegreen", project_z=True))
    for point, individuo in zip(df_ga_min['population'], range(1,21)):

        fig.add_trace(go.Scatter3d(x=[point[0]],
                    y=[point[1]],
                    z=[rastrigin(point[0], point[1])],
                    name=f'Indivíduo {individuo}'
                    ))
    fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=-0.2
    ))

    fig.show()

# Plot da função de Rastrigin
plot_rastrigin_genetic_algorithm()

##### Box Plots

In [3]:
df_custo = pd.DataFrame(columns=['Hil Climbing Restart', 'Simulated Annealing', 'Genetic Algorithm'])
df_custo['Hil Climbing Restart'] = df_hill_climbing['z']
df_custo['Simulated Annealing'] = df_simulated_annealing['z']
df_custo['Genetic Algorithm'] = df_genetic_algorithm['result']
df_custo

NameError: name 'pd' is not defined

In [47]:
df_custo.describe()

Hil Climbing Restart  Simulated Annealing  Genetic Algorithm
count           1000.000000          1000.000000        1000.000000
mean               0.074048             4.100708           1.525957
std                1.257157             0.955903           1.633904
min                0.013829             3.983114           0.995335
25%                0.013829             3.983114           0.999523
50%                0.013829             3.983114           1.004945
75%                0.013829             3.983488           1.081777
max               39.537191            17.877174          11.073371

In [52]:
custo_line_fig = px.line(df_custo, title="Redução por iteração")
custo_line_fig.update_layout(
    xaxis_title="Iteração", yaxis_title="Custo")
custo_line_fig.show()

In [2]:
df_custo

NameError: name 'df_custo' is not defined

In [50]:
px.box(df_custo, y=df_custo.columns.tolist()).update_layout(
    xaxis_title="Algoritmo", yaxis_title="Custo", title="Custo por Algoritmo")

In [54]:
df_genetic_algorithm.to_csv("./resultados/prob2/ga.csv", sep=',')
df_hill_climbing.to_csv("./resultados/prob2/hc.csv", sep=',')
df_simulated_annealing.to_csv("./resultados/prob2/sa.csv", sep=',')
df_custo.to_csv("./resultados/prob2/custo.csv", sep=',')


In [1]:
import plotly.graph_objects as go
import numpy as np

def plot_rastrigin():
    x = np.linspace(-5.12, 5.12, 100)
    y = np.linspace(-5.12, 5.12, 100)
    X, Y = np.meshgrid(x, y)
    Z = 20 + X**2 - 10 * np.cos(2 * np.pi * X) + Y**2 - 10 * np.cos(2 * np.pi * Y)
    
    fig = go.Figure(data=[go.Surface(x=X, y=Y, z=Z)])
    fig.update_layout(title='Rastrigin Function', autosize=False,
                      scene=dict(xaxis=dict(title='X'), yaxis=dict(title='Y'), zaxis=dict(title='Z')),
                      width=800, height=800)
    fig.update_traces(contours_z=dict(show=True, usecolormap=True,
                                  highlightcolor="limegreen", project_z=True))
    
    fig.show()
    fig

# Plot da função de Rastrigin
plot_rastrigin()